In [4]:
import pandas as pd
import geopandas as gpd
import networkx as nx
import sqlite3
import folium
from folium import plugins
from IPython.display import IFrame
from shapely.geometry import Point, LineString
from folium import plugins
import geopandas as gpd
import matplotlib.pyplot as plt
import contextily as ctx
import community
from IPython.display import display
import datetime
import calendar
import collections
import matplotlib.cm as cm
from matplotlib.colors import ListedColormap, LinearSegmentedColormap
import seaborn as sns
import plotly.graph_objects as go
import community as community_louvain
from operator import itemgetter
from folium import plugins
from prettytable import PrettyTable

ModuleNotFoundError: No module named 'geopandas'

In [2]:
bus_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_bus.csv', sep=',')
combined_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_combined.csv')
temporal_day_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_temporal_day.csv')
temporal_week_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_temporal_week.csv')
tram_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/venice/network_tram.csv')
walk_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_walk.csv')
nodes_network = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/network_nodes.csv')

stops = gpd.read_file('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/stops.geojson')
sections = gpd.read_file('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/sections.geojson')
routes = gpd.read_file('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/routes.geojson')

top=pd.read_excel('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/toppalermo.xlsx')
final=pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')

In [19]:
import folium
import networkx as nx
import pandas as pd
# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')
# Filter only bus routes
bus_df = final[final['BUS'] == 1]
# Create a directed graph using networkx
G = nx.DiGraph()
# Add nodes to the graph
for index, row in bus_df.iterrows():
    node_id = row['id']
    stop_name = row['name']
    G.add_node(node_id, name=stop_name)

# Create a Folium map centered around Palermo
palermo_map = folium.Map(location=[38.1157, 13.3615], zoom_start=13)
# Add nodes to the map
for node_id, data in G.nodes(data=True):
    stop_name = data.get('name', '')  # Use get to handle missing 'name' key
    
    # Extract coordinates from 'geometry_stops' column
    stop_data = final[final['id'] == node_id]['geometry_stops'].values
    if len(stop_data) > 0:
        stop_coordinates = stop_data[0]
        lon, lat = map(float, stop_coordinates[7:-1].split())  # Extracting lon and lat from 'POINT (lon lat)'

        folium.Marker(
            location=[lat, lon],
            popup=stop_name,
            icon=folium.Icon(color='green', icon='info-sign')
        ).add_to(palermo_map)

# Add edges to the graph
for index, row in bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G.add_edge(from_stop, to_stop)

# Add edges to the map as PolyLines
for edge in G.edges():
    from_stop, to_stop = edge
    
    # Extract coordinates from 'geometry_stops' column
    from_data = final[final['id'] == from_stop]['geometry_stops'].values
    to_data = final[final['id'] == to_stop]['geometry_stops'].values
    
    if len(from_data) > 0 and len(to_data) > 0:
        from_coords = from_data[0]
        to_coords = to_data[0]
        
        # Extract lon and lat from 'POINT (lon lat)'
        from_lon, from_lat = map(float, from_coords[7:-1].split())
        to_lon, to_lat = map(float, to_coords[7:-1].split())
        
        # Add PolyLine to the map
        folium.PolyLine(locations=[[from_lat, from_lon], [to_lat, to_lon]], color='blue', weight=2, opacity=0.7).add_to(palermo_map)
palermo_map

In [21]:
import folium
import networkx as nx
import pandas as pd
# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')
# Filter only bus routes
bus_df = final[final['BUS'] == 1]
# Create a directed graph using networkx
G = nx.DiGraph()
# Add nodes to the graph
for index, row in bus_df.iterrows():
    node_id = row['id']
    stop_name = row['name']
    G.add_node(node_id, name=stop_name)

# Add edges to the graph
for index, row in bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G.add_edge(from_stop, to_stop)

# Calculate centrality measures
degree_centrality = nx.degree_centrality(G)
closeness_centrality = nx.closeness_centrality(G)
betweenness_centrality = nx.betweenness_centrality(G)
eigenvector_centrality = nx.eigenvector_centrality(G)
# Get top 10 nodes for each centrality measure
top_10_degree = sorted(degree_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_closeness = sorted(closeness_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_betweenness = sorted(betweenness_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_eigenvector = sorted(eigenvector_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
# Print top 10 nodes for each centrality measure
print("Top 10 Nodes by Degree Centrality:")
for node_id, centrality in top_10_degree:
    print(f"Node {node_id}: {centrality}")
print("\nTop 10 Nodes by Closeness Centrality:")
for node_id, centrality in top_10_closeness:
    print(f"Node {node_id}: {centrality}")
print("\nTop 10 Nodes by Betweenness Centrality:")
for node_id, centrality in top_10_betweenness:
    print(f"Node {node_id}: {centrality}")
print("\nTop 10 Nodes by Eigenvector Centrality:")
for node_id, centrality in top_10_eigenvector:
    print(f"Node {node_id}: {centrality}")

Top 10 Nodes by Degree Centrality:
Node 1840: 0.007352941176470588
Node 540: 0.006433823529411764
Node 856: 0.004136029411764706
Node 1312: 0.004136029411764706
Node 1346: 0.003676470588235294
Node 1938: 0.003676470588235294
Node 873: 0.003216911764705882
Node 876: 0.003216911764705882
Node 1262: 0.003216911764705882
Node 148: 0.0027573529411764703

Top 10 Nodes by Closeness Centrality:
Node 876: 0.03553856210352318
Node 873: 0.03523558663120672
Node 959: 0.035138768358286436
Node 419: 0.03509565678519369
Node 241: 0.03503852721462824
Node 1675: 0.034959644607449
Node 875: 0.03495627186067056
Node 1189: 0.03487552071930864
Node 339: 0.034859862413553065
Node 551: 0.034827472038044656

Top 10 Nodes by Betweenness Centrality:
Node 1840: 0.22011356234245363
Node 1030: 0.13044512436314915
Node 873: 0.12307684263948507
Node 1938: 0.12095487650695039
Node 856: 0.11591061635184292
Node 1819: 0.11377783675226527
Node 890: 0.11144319741899932
Node 1019: 0.11144319741899932
Node 889: 0.107552714

In [22]:
import folium
import networkx as nx
import pandas as pd
# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')
# Filter only bus routes
bus_df = final[final['BUS'] == 1]
# Create a directed graph using networkx
G = nx.DiGraph()
# Add nodes to the graph
for index, row in bus_df.iterrows():
    node_id = row['id']
    stop_name = row['name']
    G.add_node(node_id, name=stop_name)
# Create a Folium map centered around Palermo
palermo_map = folium.Map(location=[38.1157, 13.3615], zoom_start=13)

# Add sections as edges to the graph
for index, row in bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G.add_edge(from_stop, to_stop)

# Add sections as PolyLines to the map
for edge in G.edges():
    from_stop, to_stop = edge
    
    # Extract coordinates from 'geometry_stops' column
    from_data = final[final['id'] == from_stop]['geometry_stops'].values
    to_data = final[final['id'] == to_stop]['geometry_stops'].values
    
    if len(from_data) > 0 and len(to_data) > 0:
        from_coords = from_data[0]
        to_coords = to_data[0]
        
        # Extract lon and lat from 'POINT (lon lat)'
        from_lon, from_lat = map(float, from_coords[7:-1].split())
        to_lon, to_lat = map(float, to_coords[7:-1].split())
        
        # Add PolyLine to the map
        folium.PolyLine(locations=[[from_lat, from_lon], [to_lat, to_lon]], color='blue', weight=2, opacity=0.7).add_to(palermo_map)

# Display the map in the Jupyter Notebook
palermo_map


In [24]:
# Calculate in-degree and out-degree for each node
in_degrees = dict(G.in_degree())
out_degrees = dict(G.out_degree())

# Get top 10 nodes by in-degree
top_10_in_degree = sorted(in_degrees.items(), key=lambda x: x[1], reverse=True)[:10]

# Get top 10 nodes by out-degree
top_10_out_degree = sorted(out_degrees.items(), key=lambda x: x[1], reverse=True)[:10]

# Print top 10 nodes by in-degree
print("\nTop 10 Nodes by In-Degree:")
for node_id, in_degree in top_10_in_degree:
    print(f"Node {node_id}: {in_degree}")
# Print top 10 nodes by out-degree
print("\nTop 10 Nodes by Out-Degree:")
for node_id, out_degree in top_10_out_degree:
    print(f"Node {node_id}: {out_degree}")



Top 10 Nodes by In-Degree:
Node 540: 12
Node 1840: 9
Node 1819: 5
Node 164: 4
Node 856: 4
Node 1262: 4
Node 1505: 4
Node 1946: 4
Node 103: 3
Node 148: 3

Top 10 Nodes by Out-Degree:
Node 1312: 7
Node 1840: 7
Node 1346: 6
Node 1938: 6
Node 856: 5
Node 2153: 5
Node 210: 4
Node 873: 4
Node 876: 4
Node 959: 4


In [33]:
#edge betweenness centrality
#equation 21 
# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')
# Filter only bus routes
bus_df = final[final['BUS'] == 1]
# Create a directed graph using networkx
G_palermo = nx.DiGraph()
G_palermo = nx.from_pandas_edgelist(bus_df, 'from_stop_I', 'to_stop_I', create_using=nx.DiGraph())

# Calculate edge betweenness centrality
edge_betweenness_centrality = nx.edge_betweenness_centrality(G_palermo)
# Create dataframe for top 10 edges with additional information
def create_edge_dataframe(centrality_measure):
    edges_info = [{'from_stop': edge[0], 'to_stop': edge[1],
                   'betweenness_centrality': centrality_measure[edge]}
                  for edge in sorted(centrality_measure, key=centrality_measure.get, reverse=True)[:10]]
    return pd.DataFrame(edges_info)

# Create dataframe for edge betweenness centrality
f_edge_betweenness = create_edge_dataframe(edge_betweenness_centrality)

# Display the dataframe
print("\nTop 10 edges by betweenness centrality:")
print(f_edge_betweenness)


Top 10 edges by betweenness centrality:
   from_stop  to_stop  betweenness_centrality
0       1819     1938                0.114237
1       1019      890                0.111903
2       1030     1019                0.110294
3        873      889                0.108012
4        889     1023                0.108012
5        417       93                0.104815
6       1050     1867                0.097700
7       1867      870                0.097700
8        255      254                0.095391
9        419      255                0.095391


In [35]:
#equation13 
shortest_paths = dict(nx.all_pairs_shortest_path_length(G_palermo))
# Calculate efficiency
N = len(G_palermo.nodes)
efficiency_sum = 0

for i in G_palermo.nodes:
    for j in G_palermo.nodes:
        if i != j and j in shortest_paths[i]:
            dij = shortest_paths[i][j]
            efficiency_sum += 1 / dij

# Calculate efficiency
efficiency = efficiency_sum / (N * (N - 1))
print("Efficiency of bus network:", efficiency)

Efficiency of bus network: 0.02975018054544002


In [36]:
def geodesic_vulnerability(G, v):
    # Calculate the shortest paths for all nodes
    all_shortest_paths = dict(nx.all_pairs_shortest_path_length(G))
    
    # Calculate the shortest paths when bus v is failed
    failed_shortest_paths = dict(nx.single_source_shortest_path_length(G, v))
    
    # Calculate the numerator and denominator for geodesic vulnerability
    numerator_sum = 0
    denominator_sum = 0
    
    for i in G.nodes:
        for j in G.nodes:
            if i != j and j in all_shortest_paths[i]:
                dij = all_shortest_paths[i][j]
                
                # Check if the path exists in failed_shortest_paths
                dvij = failed_shortest_paths[j] if j in failed_shortest_paths else float('inf')
                
                # Check for both infinity and zero distances
                if dij != 0 and dvij != 0 and dvij != float('inf'):
                    numerator_sum += 1 / dvij
                    denominator_sum += 1 / dij
    
    # Calculate geodesic vulnerability and normalize to [0, 1]
    geodesic_vulnerability = max(1 - (numerator_sum / denominator_sum), 0)
    
    print(f"Numerator Sum: {numerator_sum}")
    print(f"Denominator Sum: {denominator_sum}")
    print(f"Geodesic Vulnerability: {geodesic_vulnerability}")
    
    return geodesic_vulnerability

# Example: Calculate geodesic vulnerability for ferry 'v' (replace 'your_bus_id' with my actual bus ID)
your_bus_id = 135
if your_bus_id in G_palermo.nodes:
    bus_vulnerability = geodesic_vulnerability(G_palermo, your_bus_id)
    print(f"Geodesic vulnerability for bus Palermo {your_bus_id}: {bus_vulnerability}")
else:
    print(f"Bus {your_bus_id} not found in the graph.")

Numerator Sum: 156289.14151360482
Denominator Sum: 140745.68618273412
Geodesic Vulnerability: 0
Geodesic vulnerability for bus Palermo 135: 0


In [52]:
# Read the dataset for Palermo
palermo_final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')

# Filter only bus routes in Palermo
palermo_bus_df = palermo_final[palermo_final['BUS'] == 1]

# Create a directed graph for bus routes in Palermo using networkx
G_palermo_bus = nx.DiGraph()

# Add nodes and edges to the graph for bus routes in Palermo
for index, row in palermo_bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G_palermo_bus.add_edge(from_stop, to_stop)

# Function to calculate geodesic vulnerability for each node
def geodesic_vulnerability(G, v):
    # Calculate the shortest paths for all nodes
    all_shortest_paths = dict(nx.all_pairs_shortest_path_length(G))
    
    # Calculate the shortest paths when node v is failed
    failed_shortest_paths = dict(nx.single_source_shortest_path_length(G, v))
    
    # Calculate the numerator and denominator for geodesic vulnerability
    numerator_sum = 0
    denominator_sum = 0
    
    for i in G.nodes:
        for j in G.nodes:
            if i != j and j in all_shortest_paths[i]:
                dij = all_shortest_paths[i][j]
                
                # Check if the path exists in failed_shortest_paths
                dvij = failed_shortest_paths[j] if j in failed_shortest_paths else float('inf')
                
                # Check for both infinity and zero distances
                if dij != 0 and dvij != 0 and dvij != float('inf'):
                    numerator_sum += 1 / dvij
                    denominator_sum += 1 / dij
    
    # Check if denominator_sum is zero before performing the division
    if denominator_sum == 0:
        return 0
    
    # Calculate geodesic vulnerability and normalize to [0, 1]
    geodesic_vulnerability = max(1 - (numerator_sum / denominator_sum), 0)
    
    return geodesic_vulnerability

# Calculate geodesic vulnerability for each node in the bus route network in Palermo
palermo_bus_vulnerabilities = {}
for node in G_palermo_bus.nodes:
    vulnerability = geodesic_vulnerability(G_palermo_bus, node)
    palermo_bus_vulnerabilities[node] = vulnerability

df_palermo_bus_station_vulnerabilities = pd.DataFrame(list(palermo_bus_vulnerabilities.items()), columns=['id', 'Geodesic_Vulnerability'])

# Adjust column names for merging based on the actual column names in palermo_bus_df
df_palermo_bus_station_vulnerabilities = pd.merge(df_palermo_bus_station_vulnerabilities, palermo_bus_df[['stop_I', 'name', 'geometry_stops']], left_on='id', right_on='stop_I', how='left')

df_palermo_bus_station_vulnerabilities = df_palermo_bus_station_vulnerabilities[['id', 'name', 'geometry_stops', 'Geodesic_Vulnerability']]

# Display the top 10 nodes by geodesic vulnerability with additional information
top_nodes_palermo_bus = df_palermo_bus_station_vulnerabilities.nlargest(10, 'Geodesic_Vulnerability')
print("Top 10 bus stations in Palermo by geodesic vulnerability:")
print(top_nodes_palermo_bus)

Top 10 bus stations in Palermo by geodesic vulnerability:
        id                             name                   geometry_stops  \
1748  1114                    VILLAGRAZIA 1  POINT (13.35876667 38.09287667)   
1165   659        VILLAGRAZIA - PONTE ROTTO    POINT (13.356765 38.09182167)   
1166  1116                    VILLAGRAZIA 2    POINT (13.354835 38.09093333)   
1380   814      VILLAGRAZIA - DELL'USIGNOLO    POINT (13.352715 38.08958667)   
1381  1003                    EMILY BALCH 1  POINT (13.34872667 38.08894167)   
1619   997        EMILY BALCH - VILLAGRAZIA  POINT (13.34520833 38.08756333)   
1549   935  VILLAGRAZIA - DELLA VISITAZIONE  POINT (13.34360898 38.08692559)   
1375   808           VILLAGRAZIA - GIRGENTI   POINT (13.34222227 38.0870227)   
1376   812               VILLAGRAZIA - ETNA  POINT (13.33892047 38.08664587)   
1170   662           VILLAGRAZIA - MARCHESE  POINT (13.33721861 38.08463185)   

      Geodesic_Vulnerability  
1748                0.597624  

#TRAM

In [26]:
import folium
import networkx as nx
import pandas as pd

# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')

# Filter only bus routes
bus_df = final[final['TRAM'] == 1]

# Create a directed graph using networkx
G = nx.DiGraph()

# Add nodes to the graph
for index, row in bus_df.iterrows():
    node_id = row['id']
    stop_name = row['name']
    G.add_node(node_id, name=stop_name)

# Create a Folium map centered around Palermo
palermo_map = folium.Map(location=[38.1157, 13.3615], zoom_start=13)

# Add nodes to the map
for node_id, data in G.nodes(data=True):
    stop_name = data.get('name', '')  # Use get to handle missing 'name' key
    
    # Extract coordinates from 'geometry_stops' column
    stop_data = final[final['id'] == node_id]['geometry_stops'].values
    if len(stop_data) > 0:
        stop_coordinates = stop_data[0]
        lon, lat = map(float, stop_coordinates[7:-1].split())  # Extracting lon and lat from 'POINT (lon lat)'

        folium.Marker(
            location=[lat, lon],
            popup=stop_name,
            icon=folium.Icon(color='green', icon='info-sign')
        ).add_to(palermo_map)

# Add edges to the graph
for index, row in bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G.add_edge(from_stop, to_stop)

# Add edges to the map as PolyLines
for edge in G.edges():
    from_stop, to_stop = edge
    
    # Extract coordinates from 'geometry_stops' column
    from_data = final[final['id'] == from_stop]['geometry_stops'].values
    to_data = final[final['id'] == to_stop]['geometry_stops'].values
    
    if len(from_data) > 0 and len(to_data) > 0:
        from_coords = from_data[0]
        to_coords = to_data[0]
        
        # Extract lon and lat from 'POINT (lon lat)'
        from_lon, from_lat = map(float, from_coords[7:-1].split())
        to_lon, to_lat = map(float, to_coords[7:-1].split())
        
        # Add PolyLine to the map
        folium.PolyLine(locations=[[from_lat, from_lon], [to_lat, to_lon]], color='blue', weight=2, opacity=0.7).add_to(palermo_map)

# Display the map in the Jupyter Notebook
palermo_map

In [27]:
# Read the dataset
final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')

# Filter only bus routes
bus_df = final[final['TRAM'] == 1]

# Create a directed graph using networkx
G = nx.DiGraph()

# Add nodes to the graph
for index, row in bus_df.iterrows():
    node_id = row['id']
    stop_name = row['name']
    G.add_node(node_id, name=stop_name)

# Add edges to the graph
for index, row in bus_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G.add_edge(from_stop, to_stop)

# Calculate centrality measures
degree_centrality = nx.degree_centrality(G)
closeness_centrality = nx.closeness_centrality(G)
betweenness_centrality = nx.betweenness_centrality(G)
eigenvector_centrality = nx.eigenvector_centrality(G)

# Get top 10 nodes for each centrality measure
top_10_degree = sorted(degree_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_closeness = sorted(closeness_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_betweenness = sorted(betweenness_centrality.items(), key=lambda x: x[1], reverse=True)[:10]
top_10_eigenvector = sorted(eigenvector_centrality.items(), key=lambda x: x[1], reverse=True)[:10]

# Print top 10 nodes for each centrality measure
print("Top 10 Nodes by Degree Centrality:")
for node_id, centrality in top_10_degree:
    print(f"Node {node_id}: {centrality}")

print("\nTop 10 Nodes by Closeness Centrality:")
for node_id, centrality in top_10_closeness:
    print(f"Node {node_id}: {centrality}")

print("\nTop 10 Nodes by Betweenness Centrality:")
for node_id, centrality in top_10_betweenness:
    print(f"Node {node_id}: {centrality}")

print("\nTop 10 Nodes by Eigenvector Centrality:")
for node_id, centrality in top_10_eigenvector:
    print(f"Node {node_id}: {centrality}")

Top 10 Nodes by Degree Centrality:
Node 959: 0.03875968992248062
Node 961: 0.031007751937984496
Node 962: 0.023255813953488372
Node 970: 0.023255813953488372
Node 545: 0.015503875968992248
Node 947: 0.015503875968992248
Node 951: 0.015503875968992248
Node 956: 0.015503875968992248
Node 958: 0.015503875968992248
Node 965: 0.015503875968992248

Top 10 Nodes by Closeness Centrality:
Node 1889: 0.012919896640826873
Node 972: 0.012403100775193798
Node 1746: 0.012403100775193798
Node 281: 0.012403100775193798
Node 1247: 0.012403100775193798
Node 1238: 0.012403100775193798
Node 956: 0.011627906976744186
Node 968: 0.011627906976744186
Node 1743: 0.011627906976744186
Node 1753: 0.011627906976744186

Top 10 Nodes by Betweenness Centrality:
Node 959: 0.0009084302325581395
Node 962: 0.0005450581395348837
Node 961: 0.0003633720930232558
Node 1743: 0.0003633720930232558
Node 965: 0.00024224806201550387
Node 1746: 0.00024224806201550387
Node 1754: 0.00024224806201550387
Node 1758: 0.00024224806201550

In [28]:
# Calculate in-degree and out-degree for each node
in_degrees = dict(G.in_degree())
out_degrees = dict(G.out_degree())

# Get top 10 nodes by in-degree
top_10_in_degree = sorted(in_degrees.items(), key=lambda x: x[1], reverse=True)[:10]

# Get top 10 nodes by out-degree
top_10_out_degree = sorted(out_degrees.items(), key=lambda x: x[1], reverse=True)[:10]

# Print top 10 nodes by in-degree
print("\nTop 10 Nodes by In-Degree:")
for node_id, in_degree in top_10_in_degree:
    print(f"Node {node_id}: {in_degree}")

# Print top 10 nodes by out-degree
print("\nTop 10 Nodes by Out-Degree:")
for node_id, out_degree in top_10_out_degree:
    print(f"Node {node_id}: {out_degree}")


Top 10 Nodes by In-Degree:
Node 545: 1
Node 947: 1
Node 951: 1
Node 956: 1
Node 958: 1
Node 959: 1
Node 961: 1
Node 962: 1
Node 965: 1
Node 968: 1

Top 10 Nodes by Out-Degree:
Node 959: 4
Node 961: 3
Node 962: 2
Node 970: 2
Node 1763: 2
Node 548: 2
Node 459: 1
Node 460: 1
Node 461: 1
Node 462: 1


In [38]:
#edge betweenness centrality
#equation 21 

tram_df = final[final['TRAM'] == 1]

# Create a directed graph using networkx for tram routes
G_palermo_tram = nx.from_pandas_edgelist(tram_df, 'from_stop_I', 'to_stop_I', create_using=nx.DiGraph())

# Calculate edge betweenness centrality for tram routes
edge_betweenness_centrality_tram = nx.edge_betweenness_centrality(G_palermo_tram)

# Create dataframes for top 10 edges for edge betweenness centrality with additional information
def create_edge_dataframe(centrality_measure):
    edges_info = [{'from_stop': edge[0], 'to_stop': edge[1],
                   'betweenness_centrality': centrality_measure[edge]}
                  for edge in sorted(centrality_measure, key=centrality_measure.get, reverse=True)[:10]]
    return pd.DataFrame(edges_info)

# Create dataframe for edge betweenness centrality for tram routes
f_edge_betweenness_tram = create_edge_dataframe(edge_betweenness_centrality_tram)

# Display the dataframe for tram routes
print("\nTop 10 edges by betweenness centrality for tram routes:")
print(f_edge_betweenness_tram)


Top 10 edges by betweenness centrality for tram routes:
   from_stop  to_stop  betweenness_centrality
0        962      959                0.001097
1        961      962                0.000710
2        959     1743                0.000581
3        959      961                0.000516
4       1743     1746                0.000516
5        959      956                0.000387
6        965      968                0.000387
7        973      965                0.000387
8       1754     1753                0.000387
9       1755     1754                0.000387


In [40]:
#equation13 
import networkx as nx
import pandas as pd

# Assuming you have a DataFrame named 'final' with tram routes
tram_df = final[final['TRAM'] == 1]

# Create a directed graph using networkx for tram routes
G_palermo_tram = nx.from_pandas_edgelist(tram_df, 'from_stop_I', 'to_stop_I', create_using=nx.DiGraph())

# Calculate shortest paths for all pairs of nodes
shortest_paths = dict(nx.all_pairs_shortest_path_length(G_palermo_tram))

# Calculate efficiency
N = len(G_palermo_tram.nodes)
efficiency_sum = 0

for i in G_palermo_tram.nodes:
    for j in G_palermo_tram.nodes:
        if i != j and j in shortest_paths[i]:
            dij = shortest_paths[i][j]
            efficiency_sum += 1 / dij

# Calculate efficiency
efficiency = efficiency_sum / (N * (N - 1))

print("Efficiency of Palermo tram network:", efficiency)

Efficiency of Palermo tram network: 0.00629247311827957


In [42]:
import networkx as nx
import pandas as pd

# Assuming you have a DataFrame named 'final' with tram routes
tram_df = final[final['TRAM'] == 1]

# Create a directed graph using networkx for tram routes
G_palermo_tram = nx.from_pandas_edgelist(tram_df, 'from_stop_I', 'to_stop_I', create_using=nx.DiGraph())

def geodesic_vulnerability(G, v):
    # Calculate the shortest paths for all nodes
    all_shortest_paths = dict(nx.all_pairs_shortest_path_length(G))
    
    # Calculate the shortest paths when tram v is failed
    failed_shortest_paths = dict(nx.single_source_shortest_path_length(G, v))
    
    # Calculate the numerator and denominator for geodesic vulnerability
    numerator_sum = 0
    denominator_sum = 0
    
    for i in G.nodes:
        for j in G.nodes:
            if i != j and j in all_shortest_paths[i]:
                dij = all_shortest_paths[i][j]
                
                # Check if the path exists in failed_shortest_paths
                dvij = failed_shortest_paths[j] if j in failed_shortest_paths else float('inf')
                
                # Check for both infinity and zero distances
                if dij != 0 and dvij != 0 and dvij != float('inf'):
                    numerator_sum += 1 / dvij
                    denominator_sum += 1 / dij
    
    # Calculate geodesic vulnerability and normalize to [0, 1]
    geodesic_vulnerability = max(1 - (numerator_sum / denominator_sum), 0)
    
    print(f"Numerator Sum: {numerator_sum}")
    print(f"Denominator Sum: {denominator_sum}")
    print(f"Geodesic Vulnerability: {geodesic_vulnerability}")
    
    return geodesic_vulnerability

# Example: Calculate geodesic vulnerability for tram 'v' (replace 'your_tram_id' with the actual tram ID)
your_tram_id = 545
if your_tram_id in G_palermo_tram.nodes:
    tram_vulnerability = geodesic_vulnerability(G_palermo_tram, your_tram_id)
    print(f"Geodesic vulnerability for tram {your_tram_id}: {tram_vulnerability}")
else:
    print(f"Tram {your_tram_id} not found in the graph.")

Numerator Sum: 3.0
Denominator Sum: 1.8333333333333333
Geodesic Vulnerability: 0
Geodesic vulnerability for tram 545: 0


In [56]:
# Read the dataset for Palermo
palermo_final = pd.read_csv('/lustrehome/niloofar/niloofar_work/ENEA/Palermo/ok.csv')
# Filter only tram routes in Palermo
palermo_tram_df = palermo_final[palermo_final['TRAM'] == 1]
# Create a directed graph for tram routes in Palermo using networkx
G_palermo_tram = nx.DiGraph()

# Add nodes and edges to the graph for tram routes in Palermo
for index, row in palermo_tram_df.iterrows():
    from_stop = row['from_stop_I']
    to_stop = row['to_stop_I']
    G_palermo_tram.add_edge(from_stop, to_stop)

# Function to calculate geodesic vulnerability for each node
def geodesic_vulnerability(G, v):
    # Calculate the shortest paths for all nodes
    all_shortest_paths = dict(nx.all_pairs_shortest_path_length(G))
    
    # Calculate the shortest paths when node v is failed
    failed_shortest_paths = dict(nx.single_source_shortest_path_length(G, v))
    
    # Calculate the numerator and denominator for geodesic vulnerability
    numerator_sum = 0
    denominator_sum = 0
    
    for i in G.nodes:
        for j in G.nodes:
            if i != j and j in all_shortest_paths[i]:
                dij = all_shortest_paths[i][j]
                
                # Check if the path exists in failed_shortest_paths
                dvij = failed_shortest_paths[j] if j in failed_shortest_paths else float('inf')
                
                # Check for both infinity and zero distances
                if dij != 0 and dvij != 0 and dvij != float('inf'):
                    numerator_sum += 1 / dvij
                    denominator_sum += 1 / dij
    
    # Check if denominator_sum is zero before performing the division
    if denominator_sum == 0:
        return 0
    
    # Calculate geodesic vulnerability and normalize to [0, 1]
    geodesic_vulnerability = max(1 - (numerator_sum / denominator_sum), 0)
    
    return geodesic_vulnerability

# Calculate geodesic vulnerability for each node in the tram route network in Palermo
palermo_tram_vulnerabilities = {}
for node in G_palermo_tram.nodes:
    vulnerability = geodesic_vulnerability(G_palermo_tram, node)
    palermo_tram_vulnerabilities[node] = vulnerability

# Create DataFrame for tram station vulnerabilities in Palermo with additional information
df_palermo_tram_station_vulnerabilities = pd.DataFrame(list(palermo_tram_vulnerabilities.items()), columns=['id', 'Geodesic_Vulnerability'])
df_palermo_tram_station_vulnerabilities = pd.merge(df_palermo_tram_station_vulnerabilities, palermo_tram_df[['stop_I', 'name','geometry_stops']], left_on='id', right_on='stop_I', how='left')
df_palermo_tram_station_vulnerabilities = df_palermo_tram_station_vulnerabilities[['id', 'name',  'geometry_stops', 'Geodesic_Vulnerability']]

# Display the top 10 nodes by geodesic vulnerability with additional information
top_nodes_palermo_tram = df_palermo_tram_station_vulnerabilities.nlargest(10, 'Geodesic_Vulnerability')
print("Top 10 tram stations in Palermo by geodesic vulnerability:")
print(top_nodes_palermo_tram)

Top 10 tram stations in Palermo by geodesic vulnerability:
       id                            name  \
82    971         SERRADIFALCO - BERNABEI   
114  1756                      SAMBUCIA 6   
119  1760                      SAMBUCIA 1   
39    952     VITTORIO EMANUELE - BOLOGNI   
68    964          SERRADIFALCO - AURISPA   
36    950                   VILLAGRAZIA 7   
49    957  VITTORIO EMANUELE - CATTEDRALE   
62    962    INDIPENDENZA - PALAZZO REALE   
63    962    INDIPENDENZA - PALAZZO REALE   
54    961           INDIPENDENZA - PISANI   

                          geometry_stops  Geodesic_Vulnerability  
82       POINT (13.33769068 38.12802774)                0.376623  
114      POINT (13.31993167 38.08369667)                0.376623  
119      POINT (13.32584167 38.08769167)                0.376623  
39   POINT (13.3597360733 38.1150019767)                0.307692  
68      POINT (13.338169165 38.12645167)                0.250000  
36       POINT (13.36238578 38.09472675)   